In [1]:
import pandas as pd
from pathlib import Path
import numpy as np 
from tqdm import tqdm
import scapy.all
import pickle
import os
from datetime import datetime, timezone, timedelta

In [2]:
def dataframe_from_csv(target):
    return pd.read_csv(target,encoding='cp1252').rename(columns=lambda x: x.strip()).dropna(subset=['Flow ID'], how='all')

def dataframe_from_csvs(targets):
    return pd.concat([dataframe_from_csv(x) for x in targets])

In [3]:
def find_tup_pcap(df, pcap_dir):
    sip,sport,dip,dport,protocol = df[['Source IP','Source Port','Destination IP','Destination Port','Protocol']]
    protocol = 'TCP' if int(protocol) ==6 else 'UDP' if int(protocol) ==17 else 'HOPOPT'
    
    if protocol == 'HOPOPT':
        return False        
    elif protocol == 'TCP' or protocol == 'UDP':
        week = ['Monday','Tuesday','Wednesday','Thursday','Friday']
        file_path = pcap_dir + '/' + [day for day in week if pcap_dir[-3:] in day][0] +'-WorkingHours.pcap.'+protocol+'_'+sip.replace('.','-')+'_'+ str(int(sport))+'_'+dip.replace('.','-')+'_'+str(int(dport))+'.pcap'
        #pcap 파일이 50MB 보다 크면 scapy 하는데 너무 오래 걸려서 그냥 버림 
        try:
            if os.path.getsize(file_path) > 50000000:
                return False
            else:
                return scapy.sendrecv.sniff(offline = file_path)
        except OSError as e:
            print(e)
    else :
        print('Non-Exist Protocol')
        return False

In [4]:
def split_ben_mal_DF(Day_DF):
    fwd_Benign_DF = Day_DF[Day_DF['Label'] == 'BENIGN'][['Source IP', 'Source Port', 'Destination IP', 'Destination Port', 'Protocol','Label','Timestamp']]
    bwd_Benign_DF = Day_DF[Day_DF['Label'] == 'BENIGN'][['Destination IP', 'Destination Port','Source IP', 'Source Port',  'Protocol','Label','Timestamp']]
    bwd_Benign_DF.columns = ['Source IP', 'Source Port', 'Destination IP', 'Destination Port', 'Protocol','Label','Timestamp']
    Benign_DF = pd.concat([fwd_Benign_DF, bwd_Benign_DF]).drop_duplicates(subset = ['Source IP', 'Source Port', 'Destination IP', 'Destination Port', 'Protocol','Label'], keep = 'first').reset_index(drop = True)
    
    fwd_Mal_DF = Day_DF[Day_DF['Label'] != 'BENIGN'][['Source IP', 'Source Port', 'Destination IP', 'Destination Port', 'Protocol','Label','Timestamp']]
    bwd_Mal_DF = Day_DF[Day_DF['Label'] != 'BENIGN'][['Destination IP', 'Destination Port','Source IP', 'Source Port', 'Protocol','Label','Timestamp']]
    bwd_Mal_DF.columns = ['Source IP', 'Source Port', 'Destination IP', 'Destination Port', 'Protocol','Label','Timestamp']
    Mal_DF = pd.concat([fwd_Mal_DF,bwd_Mal_DF]).drop_duplicates(subset = ['Source IP', 'Source Port', 'Destination IP', 'Destination Port', 'Protocol','Label'], keep = 'first').reset_index(drop = True)

    return Benign_DF, Mal_DF

In [5]:
def drop_dup_btw_df(df1, df2):
    tmp = pd.concat([df1,df2]).reset_index(drop = True)
    dup_index = tmp[tmp.duplicated(subset = ['Source IP','Source Port','Destination IP', 'Destination Port', 'Protocol'], keep = 'last')].index
    dup_index = dup_index[dup_index < len(df1)]
    return df1.drop(index = dup_index)

In [6]:
class FlowSaver:
    def __init__(self, folder_capacity, flow_class, pkls_dir):
        self.folder_capacity = folder_capacity
        self.flow_class = flow_class
        Path(os.path.join(pkls_dir, str(self.flow_class))).mkdir(parents=True, exist_ok=True)
        self.pkls_dir = pkls_dir
        self.index = 0
        self.num = 0
        Path(os.path.join(pkls_dir, str(self.flow_class), str(self.index))).mkdir(parents=True, exist_ok=True)
        
        current_dir = sorted([x for x in Path(pkls_dir +'/'+str(self.flow_class)).glob('*')], key = lambda x : int(x.stem))[-1]         
        self.index = int(current_dir.stem)
        self.num = len([x for x in current_dir.glob('*.pkl')])
        
    def save_flow(self, flow_array):
        if self.num==self.folder_capacity:
            self.new_folder()
        pkl_path = os.path.join(pkls_dir, str(self.flow_class), str(self.index), f'{self.flow_class}_{self.index}{self.num:04d}.pkl')
        with open(pkl_path, 'wb') as f:
            pickle.dump(flow_array, f)
        self.num+=1
    
    def new_folder(self):
        self.index+=1
        self.num = 0
        Path(os.path.join(pkls_dir, str(self.flow_class), str(self.index))).mkdir(parents=True, exist_ok=True) 

In [7]:
def data_labelling(Day_DF, Day_pcap_dir,normal_saver, attack_saver):
    
    Benign_DF ,Mal_DF = split_ben_mal_DF(Day_DF)
    
    # Pure_Mal_DF : Mal flow 중에서 5tup이 중복되는게 없는 flow 
    # dup_Mal_DF : Mal flow 중에서 5tup이 중복되는게 있는 flow
    Mal_dup_list = Mal_DF.duplicated(subset = ['Source IP', 'Source Port', 'Destination IP', 'Destination Port', 'Protocol'],keep = False)    
    pure_Mal_DF = Mal_DF[~Mal_dup_list]
    dup_Mal_DF = Mal_DF[Mal_dup_list]
    
    #Benign flow에서 Mal flow와 5tup 같은 플로우 삭제
    pure_Benign_DF = drop_dup_btw_df(Benign_DF,Mal_DF)
    
    #pure_Malicous flow-> Malicious flow로 라벨링
    #pure Benign flow -> Benign flow로 라벨링
    
    for ben_idx in tqdm(range(len(pure_Benign_DF))): 
        pcks = find_tup_pcap(pure_Benign_DF.iloc[ben_idx], Day_pcap_dir)
        
        if pcks:
            #flow : 하루 동안의 5tup이 같은 패킷들을 하나의 flow로 정의
            flow_array = []
            for i in range(len(pcks)):
                flow_array.append(bytes(pcks[i]))
            normal_saver.save_flow(flow_array)
    print('Labelling pure Benign Data Finished!!!')
    
    for pmal_idx in tqdm(range(len(pure_Mal_DF))):
        pcks = find_tup_pcap(pure_Mal_DF.iloc[pmal_idx], Day_pcap_dir)
        label = pure_Mal_DF.iloc[pmal_idx]['Label']
        
        if pcks:
            #flow : 하루 동안의 5tup이 같은 패킷들을 하나의 flow로 정의
            flow_array = []
            for i in range(len(pcks)):
                flow_array.append(bytes(pcks[i]))
            attack_saver[label].save_flow(flow_array)
    print('Labelling Pure Mal Data Finished!!!')
    
    #Mallicious Flow 중 5tup 같은데 label이 다른 경우 -> pcap 파일에서 Timestamp를 기준으로 라벨링을 따로 해줘야 됨
    if not dup_Mal_DF.empty:
        for _, flows in tqdm(dup_Mal_DF.groupby(['Source IP', 'Source Port', 'Destination IP', 'Destination Port', 'Protocol'])):
            pcks = find_tup_pcap(flows.iloc[0], Day_pcap_dir)            
            # Monday csv 파일만 flow를 초 단위로 구분
            if Day_pcap_dir[-3:] == 'Mon':
                time_label = {datetime.strptime(flow['Timestamp'],'%d/%m/%Y %H:%M:%S'): flow['Label'] for _, flow in flows.iterrows()}
            else:
                time_label = {datetime.strptime(flow['Timestamp'],'%d/%m/%Y %H:%M') : flow['Label'] for _, flow in flows.iterrows()}

            tmp = 0
            for i in range(len(time_label)):
                time, label = sorted(time_label.items())[i]
                time_unit = timedelta(seconds =1) if Day_pcap_dir[-3:] == 'Mon' else timedelta(minutes=1)  
                time += time_unit
                for p_idx in range(tmp,len(pcks)):
                    if ((datetime.fromtimestamp(pcks[p_idx].time) - timedelta(hours = 12)) >= time) or (p_idx == (len(pcks) -1)):
                        flow_array = []
                        if (p_idx == (len(pcks) -1)) or (i == len(time_label) -1):
                            p_idx = len(pcks)
                        for j in range(tmp,p_idx):
                            flow_array.append(bytes(pcks[j]))
                        attack_saver[label].save_flow(flow_array)
                        tmp = p_idx
                        break

In [8]:
Wed_pcap_dir = '../../../dataset/CICIDS2017/split_pcaps/Wed'
#Wed_pcap_files = sorted([x for x in Path(Wed_pcap_dir).glob('*.pcap')])

Wednesday_csv= sorted([x for x in Path('../../../dataset/CICIDS2017/flow_label/TrafficLabelling').glob('Wednesday-*.csv')],reverse = True)
# Morning - Afternoon 순서로 정리하기 위해서

Wednesday_DF_RAW = dataframe_from_csvs(Wednesday_csv)
Wednesday_DF = Wednesday_DF_RAW.drop_duplicates(subset = ['Source IP', 'Source Port', 'Destination IP', 'Destination Port', 'Protocol','Label'], keep = 'first')
# (1분 단위로 동일한 flow를 서로 다른 flow로 분류해놓아서) 5-tuple이 같으면 동일한 flow로 분류 

pkls_dir = '../../../dataset/CICIDS2017/pkls'

In [9]:
attack_class_list = ['FTP-Patator', 'SSH-Patator', 'DoS slowloris','DoS Slowhttptest', 'DoS Hulk', 'DoS GoldenEye', 'Heartbleed','Infiltration', 'Web Attack – Brute Force', 'Web Attack – XSS','Web Attack – Sql Injection', 'DDoS', 'PortScan', 'Bot']
attack_class = {flow : i+1 for i, flow in enumerate(attack_class_list)}

normal = FlowSaver(10000,0,pkls_dir)
attack = {label : FlowSaver(10000,flow_class,pkls_dir) for label, flow_class in attack_class.items()}

In [10]:
Day_DF = Wednesday_DF
Day_pcap_dir = Wed_pcap_dir

data_labelling(Day_DF,Day_pcap_dir,normal,attack)

 37%|███▋      | 157333/425298 [28:38<22:09, 201.60it/s]  

[Errno 2] No such file or directory: '../../../dataset/CICIDS2017/split_pcaps/Wed/Wednesday-WorkingHours.pcap.UDP_192-168-10-12_43679_192-168-10-3_88.pcap'


 37%|███▋      | 158927/425298 [28:45<16:26, 270.08it/s]

[Errno 2] No such file or directory: '../../../dataset/CICIDS2017/split_pcaps/Wed/Wednesday-WorkingHours.pcap.UDP_192-168-10-17_53_192-168-10-3_10008.pcap'


 37%|███▋      | 159173/425298 [28:46<17:20, 255.82it/s]

...

  0%|          | 12/6082 [00:00<01:04, 94.26it/s]

Labelling pure Benign Data Finished!!!


100%|██████████| 6082/6082 [03:22<00:00, 30.11it/s]


Labelling Pure Mal Data Finished!!!


100%|██████████| 22156/22156 [12:38<00:00, 29.19it/s]


In [20]:
Tue_pcap_dir = '../../../dataset/CICIDS2017/split_pcaps/Tue'
#Wed_pcap_files = sorted([x for x in Path(Wed_pcap_dir).glob('*.pcap')])

Tuesday_csv= sorted([x for x in Path('../../../dataset/CICIDS2017/flow_label/TrafficLabelling').glob('Tuesday-*.csv')],reverse = True)
# Morning - Afternoon 순서로 정리하기 위해서

Tuesday_DF_RAW = dataframe_from_csvs(Tuesday_csv)
Tuesday_DF = Tuesday_DF_RAW.drop_duplicates(subset = ['Source IP', 'Source Port', 'Destination IP', 'Destination Port', 'Protocol','Label'], keep = 'first')
# (1분 단위로 동일한 flow를 서로 다른 flow로 분류해놓아서) 5-tuple이 같으면 동일한 flow로 분류 

pkls_dir = '../../../dataset/CICIDS2017/pkls'

Day_DF = Tuesday_DF
Day_pcap_dir = Tue_pcap_dir


In [24]:
data_labelling(Day_DF,Day_pcap_dir,normal,attack)

 39%|███▊      | 158421/409316 [36:35<18:27, 226.58it/s]   

[Errno 2] No such file or directory: '../../../dataset/CICIDS2017/split_pcaps/Tue/Tuesday-WorkingHours.pcap.UDP_192-168-10-50_35815_192-168-10-3_88.pcap'


 39%|███▉      | 159046/409316 [36:38<16:48, 248.22it/s]

[Errno 2] No such file or directory: '../../../dataset/CICIDS2017/split_pcaps/Tue/Tuesday-WorkingHours.pcap.UDP_192-168-10-50_44363_192-168-10-3_88.pcap'


 39%|███▉      | 159850/409316 [36:42<21:47, 190.74it/s]

...

[Errno 2] No such file or directory: '../../../dataset/CICIDS2017/split_pcaps/Tue/Tuesday-WorkingHours.pcap.UDP_192-168-10-3_29773_192-168-10-51_53.pcap'
[Errno 2] No such file or directory: '../../../dataset/CICIDS2017/split_pcaps/Tue/Tuesday-WorkingHours.pcap.UDP_162-248-16-24_137_192-168-10-8_137.pcap'


  0%|          | 0/13940 [00:00<?, ?it/s]

[Errno 2] No such file or directory: '../../../dataset/CICIDS2017/split_pcaps/Tue/Tuesday-WorkingHours.pcap.TCP_54-175-83-148_443_192-168-10-19_53764.pcap'
[Errno 2] No such file or directory: '../../../dataset/CICIDS2017/split_pcaps/Tue/Tuesday-WorkingHours.pcap.UDP_216-104-218-219_137_192-168-10-8_137.pcap'
Labelling pure Benign Data Finished!!!


100%|██████████| 13940/13940 [02:16<00:00, 102.36it/s]

Labelling Pure Mal Data Finished!!!


In [35]:
Thu_pcap_dir = '../../../dataset/CICIDS2017/split_pcaps/Thu'
#Thu_pcap_files = sorted([x for x in Path(Thu_pcap_dir).glob('*.pcap')])

Thursday_csv= sorted([x for x in Path('../../../dataset/CICIDS2017/flow_label/TrafficLabelling').glob('Thursday-*.csv')],reverse = True)
# Morning - Afternoon 순서로 정리하기 위해서

Thursday_DF_RAW = dataframe_from_csvs(Thursday_csv)
Thursday_DF = Thursday_DF_RAW.drop_duplicates(subset = ['Source IP', 'Source Port', 'Destination IP', 'Destination Port', 'Protocol','Label'], keep = 'first')
# (1분 단위로 동일한 flow를 서로 다른 flow로 분류해놓아서) 5-tuple이 같으면 동일한 flow로 분류 

Day_DF = Thursday_DF
Day_pcap_dir = Thu_pcap_dir

data_labelling(Day_DF,Day_pcap_dir,normal,attack)

/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:7: DtypeWarning: Columns (0,1,3,6,84) have mixed types.Specify dtype option on import or set low_memory=False.
  import sys


In [39]:
data_labelling(Day_DF,Day_pcap_dir,normal,attack)

  0%|          | 185/513564 [00:06<5:11:09, 27.50it/s] 

[Errno 2] No such file or directory: '../../../dataset/CICIDS2017/split_pcaps/Thu/Thursday-WorkingHours.pcap.UDP_192-168-10-12_45763_192-168-10-3_88.pcap'
[Errno 2] No such file or directory: '../../../dataset/CICIDS2017/split_pcaps/Thu/Thursday-WorkingHours.pcap.UDP_192-168-10-12_40453_192-168-10-3_88.pcap'
[Errno 2] No such file or directory: '../../../dataset/CICIDS2017/split_pcaps/Thu/Thursday-WorkingHours.pcap.UDP_192-168-10-50_49588_192-168-10-3_88.pcap'


  0%|          | 279/513564 [00:07<2:42:17, 52.71it/s]

[Errno 2] No such file or directory: '../../../dataset/CICIDS2017/split_pcaps/Thu/Thursday-WorkingHours.pcap.UDP_192-168-10-15_53_192-168-10-3_63710.pcap'


  0%|          | 379/513564 [00:10<2:03:56, 69.01it/s]

...

  0%|          | 15/4000 [00:00<00:26, 149.65it/s]

Labelling pure Benign Data Finished!!!


 25%|██▌       | 3/12 [00:00<00:00, 19.20it/s]

Labelling Pure Mal Data Finished!!!


100%|██████████| 12/12 [00:00<00:00, 32.26it/s]


In [68]:
Fri_pcap_dir = '../../../dataset/CICIDS2017/split_pcaps/Fri'
#Thu_pcap_files = sorted([x for x in Path(Thu_pcap_dir).glob('*.pcap')])

Friday_csv= sorted([x for x in Path('../../../dataset/CICIDS2017/flow_label/TrafficLabelling').glob('Friday-*.csv')],reverse = True)
# Morning - Afternoon 순서로 정리하기 위해서

Friday_DF_RAW = dataframe_from_csvs(Friday_csv)
Friday_DF = Friday_DF_RAW.drop_duplicates(subset = ['Source IP', 'Source Port', 'Destination IP', 'Destination Port', 'Protocol','Label'], keep = 'first')
# (1분 단위로 동일한 flow를 서로 다른 flow로 분류해놓아서) 5-tuple이 같으면 동일한 flow로 분류 

Day_DF = Friday_DF
Day_pcap_dir = Fri_pcap_dir

data_labelling(Day_DF,Day_pcap_dir,normal,attack)

  0%|          | 124/383300 [00:04<3:15:00, 32.75it/s]

[Errno 2] No such file or directory: '../../../dataset/CICIDS2017/split_pcaps/Fri/Friday-WorkingHours.pcap.UDP_192-168-10-14_53_192-168-10-3_53408.pcap'


  0%|          | 145/383300 [00:04<2:25:39, 43.84it/s]

[Errno 2] No such file or directory: '../../../dataset/CICIDS2017/split_pcaps/Fri/Friday-WorkingHours.pcap.UDP_192-168-10-14_53_192-168-10-3_49954.pcap'


  1%|          | 3045/383300 [00:42<2:26:08, 43.36it/s] 

...

  0%|          | 0/409536 [00:00<?, ?it/s]

[Errno 2] No such file or directory: '../../../dataset/CICIDS2017/split_pcaps/Fri/Friday-WorkingHours.pcap.TCP_205-174-165-73_8080_192-168-10-8_10390.pcap'
Labelling pure Benign Data Finished!!!


  4%|▎         | 19/528 [00:00<00:02, 187.19it/s]

Labelling Pure Mal Data Finished!!!


100%|██████████| 528/528 [00:04<00:00, 108.96it/s]


In [91]:
Mon_pcap_dir = '../../../dataset/CICIDS2017/split_pcaps/Mon'
#Thu_pcap_files = sorted([x for x in Path(Thu_pcap_dir).glob('*.pcap')])

Monday_csv= sorted([x for x in Path('../../../dataset/CICIDS2017/flow_label/TrafficLabelling').glob('Monday-*.csv')],reverse = True)
# Morning - Afternoon 순서로 정리하기 위해서

Monday_DF_RAW = dataframe_from_csvs(Monday_csv)
Monday_DF = Monday_DF_RAW.drop_duplicates(subset = ['Source IP', 'Source Port', 'Destination IP', 'Destination Port', 'Protocol','Label'], keep = 'first')
# (1분 단위로 동일한 flow를 서로 다른 flow로 분류해놓아서) 5-tuple이 같으면 동일한 flow로 분류 

Day_DF = Monday_DF
Day_pcap_dir = Mon_pcap_dir

#data_labelling(Day_DF,Day_pcap_dir,normal,attack)

In [94]:
data_labelling(Day_DF,Day_pcap_dir,normal,attack)

  5%|▌         | 25817/498426 [06:17<1:19:48, 98.70it/s]  

[Errno 2] No such file or directory: '../../../dataset/CICIDS2017/split_pcaps/Mon/Monday-WorkingHours.pcap.UDP_192-168-10-19_53_192-168-10-3_5232.pcap'


 42%|████▏     | 207103/498426 [30:09<21:49, 222.45it/s]  

[Errno 2] No such file or directory: '../../../dataset/CICIDS2017/split_pcaps/Mon/Monday-WorkingHours.pcap.UDP_192-168-10-19_53_192-168-10-3_24654.pcap'
[Errno 2] No such file or directory: '../../../dataset/CICIDS2017/split_pcaps/Mon/Monday-WorkingHours.pcap.UDP_192-168-10-19_53_192-168-10-3_30611.pcap'


 42%|████▏     | 207218/498426 [30:09<19:43, 246.12it/s]

...

[Errno 2] No such file or directory: '../../../dataset/CICIDS2017/split_pcaps/Mon/Monday-WorkingHours.pcap.UDP_255-255-255-255_3289_192-168-10-51_57602.pcap'
[Errno 2] No such file or directory: '../../../dataset/CICIDS2017/split_pcaps/Mon/Monday-WorkingHours.pcap.UDP_224-0-0-252_5355_192-168-10-3_53949.pcap'


100%|█████████▉| 498374/498426 [58:02<00:00, 255.71it/s]

[Errno 2] No such file or directory: '../../../dataset/CICIDS2017/split_pcaps/Mon/Monday-WorkingHours.pcap.TCP_52-72-182-110_443_192-168-10-5_63185.pcap'
[Errno 2] No such file or directory: '../../../dataset/CICIDS2017/split_pcaps/Mon/Monday-WorkingHours.pcap.UDP_255-255-255-255_1124_192-168-10-50_54402.pcap'
[Errno 2] No such file or directory: '../../../dataset/CICIDS2017/split_pcaps/Mon/Monday-WorkingHours.pcap.UDP_192-168-10-255_137_192-168-10-12_39450.pcap'


100%|██████████| 498426/498426 [58:02<00:00, 143.11it/s]
0it [00:00, ?it/s]

Labelling pure Benign Data Finished!!!
Labelling Pure Mal Data Finished!!!


In [95]:
import os
import glob
import pickle
import numpy as np
import torch
from torch.utils.data import Dataset, DataLoader


def has_file_allowed_extension(filename, extensions):
    return filename.lower().endswith(extensions)

def make_dataset(directory, class_to_idx, extensions='.pkl'):
    instances = []
    directory = os.path.expanduser(directory)
    def is_valid_file(x):
        return has_file_allowed_extension(x, extensions)
    for target_class in sorted(class_to_idx.keys()):
        class_index = class_to_idx[target_class]
        target_dir = os.path.join(directory, target_class)
        if not os.path.isdir(target_dir):
            continue
        for root, _, fnames in sorted(os.walk(target_dir, followlinks=True)):
            for fname in sorted(fnames):
                path = os.path.join(root, fname)
                if is_valid_file(path):
                    item = path, class_index
                    instances.append(item)
    return instances

class PklsFolder(Dataset):
    def __init__(self, root_dir):
        classes, class_to_idx = self._find_classes(root_dir)
        samples = make_dataset(root_dir, class_to_idx)
        self.classes = classes
        self.class_to_idx = class_to_idx
        self.samples = samples
        self.targets = [s[1] for s in samples]

    def _find_classes(self, dir):
        classes = [d.name for d in os.scandir(dir) if d.is_dir()]
        classes.sort(key = lambda x : int(x))
        class_to_idx = {cls_name: i for i, cls_name in enumerate(classes)}
        return classes, class_to_idx

    def __getitem__(self, index):
        path, target = self.samples[index]
        with open(path, 'rb') as f:
            sample = pickle.load(f)
        flow = np.zeros([128, 1500])
        #for i in range(len(sample)):
        for i in range(min(128,len(sample))):
            flow[i, :len(sample[i])] = np.frombuffer(sample[i][:1500], dtype=np.uint8)
            #randomize MAC,IP addresses
            flow[i, 0:12] = np.random.randint(256, size = 12, dtype = np.uint8)
            flow[i, 26:34] = np.random.randint(256, size = 8, dtype = np.uint8)
        return flow, target

    def __len__(self):
        return len(self.samples)
    
    def data_cnt_per_class(self):
        class_cnt = {label : 0 for label in self.classes}
        for i in range(len(self.targets)):
            class_cnt[str(self.targets[i])] += 1
        return class_cnt

In [96]:
flow_dataset = PklsFolder(pkls_dir)

In [97]:
len(flow_dataset)

2679226

In [98]:
flow_dataset.data_cnt_per_class()

{'0': 2191361,
 '1': 7982,
 '2': 5958,
 '3': 7746,
 '4': 8432,
 '5': 28216,
 '6': 14916,
 '7': 1,
 '8': 12,
 '9': 2726,
 '10': 1262,
 '11': 24,
 '12': 90784,
 '13': 317350,
 '14': 2456}

In [ ]:
flow를 구성하는 패킷의 수, 패킷의 길이 정해서 PklsFolder 클래스 코드 수정해야됨